In [86]:
# imports
import pandas as pd
import numpy as np
import plotly.express as px
pd.options.plotting.backend = "plotly"
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

from sktime.forecasting.model_selection import temporal_train_test_split
from sktime.forecasting.model_evaluation import evaluate
from sktime.forecasting.trend import PolynomialTrendForecaster
from sktime.transformations.series.detrend import (
    Detrender,
    Deseasonalizer
    )
from sktime.forecasting.compose import (
    ForecastingPipeline, 
    TransformedTargetForecaster)
from sktime.forecasting.naive import NaiveForecaster
from sktime.forecasting.arima import ARIMA
from sktime.transformations.series.date import DateTimeFeatures
from sktime.transformations.series.adapt import TabularToSeriesAdaptor
from sktime.forecasting.base import ForecastingHorizon
from sktime.forecasting.compose import make_reduction
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from sklearn.preprocessing import (
    StandardScaler, 
    MinMaxScaler
    )
from sktime.performance_metrics.forecasting import (
    MeanAbsoluteScaledError,
    MeanAbsoluteError,
    MeanAbsolutePercentageError,
    MeanSquaredError,
    )
mase = MeanAbsoluteScaledError()
mape = MeanAbsolutePercentageError()
mae = MeanAbsoluteError()
rmse = MeanSquaredError(square_root=True)

from sktime.transformations.series.summarize import WindowSummarizer
from sktime.forecasting.model_selection import (
    SlidingWindowSplitter,
    ForecastingRandomizedSearchCV,
    ForecastingGridSearchCV,
    )


horizon = 7
sp = 7
cv_folds = 4

# data prep

In [45]:
# load data 
df_store = pd.read_pickle("data/df_daily.pkl")
df_store['sales'] = df_store['sales']/1e6
df_exog = pd.read_pickle("data/df_exog.pkl")
ts_company = df_store.groupby("date").sum()["sales"]


In [88]:
df_exog = pd.read_pickle("data/df_exog.pkl")
ts_y = ts_company

# extract lags, means, medians
kwargs = {
    "lag_config": {
        "lag": ["lag", [[1,i+6] for i in range(horizon)]], 
            # sales_lag_1_6 = lag 7
        "expand_mean": ["mean", [[i,horizon-1] for i in range(2, horizon+1)]], 
            # sales_expand_mean_2_6 = mean of 2 lags starting from lag 7, i.e lag 7 & lag 8
            # sales_expand_mean_3_6 = mean of 3 lags starting from lag 7, i.e lag 7 & lag 8 & lag 9
            # etc.
        }}
df_window = WindowSummarizer(**kwargs).fit_transform(ts_y).dropna()

# extract DateTimeFeatures
df_from_y = DateTimeFeatures(ts_freq="D", feature_scope="comprehensive").fit_transform(df_window)
df_X = df_exog.merge(df_from_y, left_index=True, right_index=True)

# train/test split
y_train, y_test, X_train, X_test = temporal_train_test_split(
    X=df_X, 
    y=ts_y.tail(len(df_window)), 
    test_size=horizon)
y_train.index.freq = 'D'

# forecast horizon
fh = ForecastingHorizon(X_test.index, is_relative=False)

# transform X
scaler = TabularToSeriesAdaptor(StandardScaler())
X_train_trans = scaler.fit_transform(X_train)
X_test_trans = scaler.transform(X_test)



/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/datatypes/_series/_check.py:43: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  VALID_INDEX_TYPES = (pd.Int64Index, pd.RangeIndex, pd.PeriodIndex, pd.DatetimeIndex)
/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/datatypes/_series/_check.py:43: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  VALID_INDEX_TYPES = (pd.Int64Index, pd.RangeIndex, pd.PeriodIndex, pd.DatetimeIndex)
/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/datatypes/_series/_check.py:43: FutureWarning: pandas.Int64Index is deprecated and will be removed fro

In [97]:
# round(X_train_trans, 3)['sales_lag_1_6'].boxplot()
px.box(X_train_trans['sales_lag_1_6'])

In [ ]:
pipe_X = ForecastingPipeline([
    ("deseasonalize", Deseasonalizer(model="additive", sp=sp)),
    ("detrend", Detrender(forecaster=PolynomialTrendForecaster(degree=1))),
    ("scale", TabularToSeriesAdaptor(MinMaxScaler())),
    ])
pipe_X.fit(ts_y)

In [98]:
X_train_trans.columns
X_train.describe()
X_train_trans.describe()

off_day     promo_day  sales_lag_1_6  sales_lag_1_7  sales_lag_1_8  \
count  1254.000000  1.254000e+03   1.254000e+03   1.254000e+03   1.254000e+03   
mean      0.000000 -1.133242e-17  -3.003091e-16  -1.756525e-16   4.532968e-17   
std       1.000399  1.000399e+00   1.000399e+00   1.000399e+00   1.000399e+00   
min      -0.130505 -3.810584e-01  -1.225948e+00  -1.225181e+00  -1.223579e+00   
25%      -0.130505 -3.810584e-01  -5.352134e-01  -5.337466e-01  -5.321760e-01   
50%      -0.130505 -3.810584e-01  -3.114019e-01  -3.100059e-01  -3.086325e-01   
75%      -0.130505 -3.810584e-01   1.922560e-01   1.924722e-01   1.928263e-01   
max       7.662525  2.624270e+00   9.595726e+00   9.613555e+00   9.620699e+00   

       sales_lag_1_9  sales_lag_1_10  sales_lag_1_11  sales_lag_1_12  \
count   1.254000e+03    1.254000e+03    1.254000e+03    1.254000e+03   
mean    1.019918e-16   -1.473215e-16   -4.532968e-17    1.019918e-16   
std     1.000399e+00    1.000399e+00    1.000399e+00    1.000399e+00   
min    -1.221655e+00   -1.219810e+00   -1.217813e+00   -1.215978e+00   
25%    -5.311132e-01   -5.297746e-01   -5.283796e-01   -5.275832e-01   
50%    -3.076047e-01   -3.069633e-01   -3.063372e-01   -3.061072e-01   
75%     1.897709e-01    1.878215e-01    1.874879e-01    1.849239e-01   
max     9.618497e+00    9.616378e+00    9.613504e+00    9.609194e+00   

       sales_expand_mean_2_6  ...       quarter         month  week_of_year  \
count           1.254000e+03  ...  1.254000e+03  1.254000e+03  1.254000e+03   
mean           -2.266484e-17  ...  8.499315e-17 -6.799452e-17 -1.699863e-17   
std             1.000399e+00  ...  1.000399e+00  1.000399e+00  1.000399e+00   
min            -1.330167e+00  ... -1.409897e+00 -1.640326e+00 -1.742394e+00   
25%            -5.425412e-01  ... -5.316006e-01 -7.945328e-01 -9.032404e-01   
50%            -2.807139e-01  ...  3.466960e-01  5.126018e-02  6.501354e-02   
75%             1.887762e-01  ...  1.224993e+00  8.970531e-01  9.041670e-01   
max             8.757618e+00  ...  1.224993e+00  1.460915e+00  1.614220e+00   

                day  month_of_quarter  week_of_quarter  day_of_quarter  \
count  1.254000e+03      1.254000e+03     1.254000e+03    1.254000e+03   
mean  -5.312072e-17      2.153160e-16    -9.915868e-18    1.189904e-16   
std    1.000399e+00      1.000399e+00     1.000399e+00    1.000399e+00   
min   -1.678506e+00     -1.415490e+00    -4.897024e-02   -1.705615e+00   
25%   -8.828087e-01     -3.564062e-01    -4.897023e-02   -8.790676e-01   
50%    2.655950e-02     -3.564062e-01    -4.897021e-02    2.262009e-02   
75%    8.222567e-01      7.026776e-01    -4.897019e-02    8.773448e-01   
max    1.731625e+00      1.761761e+00     2.042058e+01    1.713284e+00   

       week_of_month           day       weekday  
count   1.254000e+03  1.254000e+03  1.254000e+03  
mean   -7.791039e-17 -5.312072e-17 -7.295245e-17  
std     1.000399e+00  1.000399e+00  1.000399e+00  
min    -1.343821e+00 -1.678506e+00 -1.500450e+00  
25%    -5.559988e-01 -8.828087e-01 -1.000698e+00  
50%     2.318232e-01  2.655950e-02 -1.195577e-03  
75%     1.019645e+00  8.222567e-01  9.983071e-01  
max     1.807467e+00  1.731625e+00  1.498058e+00  

[8 rows x 26 columns]

In [99]:
# use XGB as forecaster
forecaster = make_reduction(
    estimator=XGBRegressor(eval_metric=mae), 
    window_length=sp, 
    strategy="recursive",
    )

# pipeline for tuning
pipe = TransformedTargetForecaster([
    # ("deseasonalize", Deseasonalizer(model="additive", sp=sp)),
    # ("detrend", Detrender(forecaster=PolynomialTrendForecaster(degree=1))),
    # ("scale", scaler),
    ("forecaster", forecaster),
    ])

# config CV
cv = SlidingWindowSplitter(
    fh=[i for i in range(1, horizon+1)],
    window_length=(len(y_train) - len(y_test) * cv_folds),
    step_length=horizon,
    )


In [77]:
cv


SlidingWindowSplitter(fh=[1, 2, 3, 4, 5, 6, 7], step_length=7,
           window_length=1226)

# tuning

## random search

In [16]:
horizon=7
cv_folds=4

# TUNE with RANDOM-SEARCH
param_grid = {
    "forecaster__estimator__subsample": np.arange(0.1, 1.1, 0.1).tolist(),
    "forecaster__estimator__n_estimators": list(range(1,1000)),
    "forecaster__estimator__max_depth": list(range(1,50)),
    "forecaster__estimator__learning_rate": [0.0001, 0.001, 0.01, 0.1, 1.0],
    "forecaster__estimator__colsample_bytree": np.arange(0.1, 1.1, 0.1).tolist(),
}

rscv = ForecastingRandomizedSearchCV(
    pipe, 
    strategy="refit", 
    cv=cv, 
    param_distributions=param_grid, 
    n_iter=1,
    n_jobs=-1,   
)

y_train.index.freq = 'D'
rscv.fit(y_train, X=X_train_trans)
rscv_y_pred = rscv.predict(fh=fh, X=X_test_trans)


/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/forecasting/base/_fh.py:110: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  values = pd.Int64Index(values, dtype=int)
/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/utils/datetime.py:77: FutureWarning: Timestamp.freqstr is deprecated and will be removed in a future version.
  if hasattr(x, "freqstr"):
/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/utils/datetime.py:78: FutureWarning: Timestamp.freqstr is deprecated and will be removed in a future version.
  if x.freqstr is None:
/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/utils/datetime.py:80: FutureWa

In [19]:
rscv.best_params_


{'forecaster__estimator__subsample': 0.30000000000000004,
 'forecaster__estimator__n_estimators': 692,
 'forecaster__estimator__max_depth': 7,
 'forecaster__estimator__learning_rate': 0.1,
 'forecaster__estimator__colsample_bytree': 0.4}

## grid search

In [23]:
# TUNE with GRID-SEARCH
param_grid = {
    "forecaster__estimator__subsample":         [0.25, 0.3, 0.35],
    "forecaster__estimator__n_estimators":      [690, 692, 695],
    "forecaster__estimator__max_depth":         [7],
    "forecaster__estimator__learning_rate":     [0.05, 0.1, 0.15],
    "forecaster__estimator__colsample_bytree":  [0.35, 0.4, 0.45],
}

gscv = ForecastingGridSearchCV(
    forecaster=pipe, 
    strategy="refit", 
    cv=cv, 
    param_grid=param_grid, 
    n_jobs=-1,
    # verbose=1,
    # refit=False,
)

gscv.fit(y_train, X=X_train_trans)


/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/forecasting/base/_fh.py:110: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  values = pd.Int64Index(values, dtype=int)
/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/forecasting/base/_fh.py:110: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  values = pd.Int64Index(values, dtype=int)
/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/forecasting/base/_fh.py:110: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  values = p

In [25]:
gscv.cv_results_.sort_values('rank_test_MeanAbsolutePercentageError').head(3)


mean_test_MeanAbsolutePercentageError  mean_fit_time  mean_pred_time  \
68                               0.195956      24.856131        0.089817   
65                               0.196561      24.368742        0.084945   
39                               0.204490      24.383529        0.085713   

                                               params  \
68  {'forecaster__estimator__colsample_bytree': 0....   
65  {'forecaster__estimator__colsample_bytree': 0....   
39  {'forecaster__estimator__colsample_bytree': 0....   

    rank_test_MeanAbsolutePercentageError  
68                                    1.0  
65                                    2.0  
39                                    3.5

In [ ]:
gscv.cv_results_.sort_values('rank_test_MeanAbsolutePercentageError').head(3)


mean_test_MeanAbsolutePercentageError  mean_fit_time  mean_pred_time  \
11                               0.242049      19.596833        0.100129   
23                               0.244141      27.820820        0.066019   
21                               0.244979      27.594359        0.113007   

                                               params  \
11  {'forecaster__estimator__colsample_bytree': 0....   
23  {'forecaster__estimator__colsample_bytree': 0....   
21  {'forecaster__estimator__colsample_bytree': 0....   

    rank_test_MeanAbsolutePercentageError  
11                                    1.0  
23                                    2.0  
21                                    3.0

In [21]:
gscv.best_params_


{'forecaster__estimator__colsample_bytree': 0.3,
 'forecaster__estimator__learning_rate': 0.2,
 'forecaster__estimator__max_depth': 6,
 'forecaster__estimator__n_estimators': 700,
 'forecaster__estimator__subsample': 0.3}

## result

In [102]:
# use default XGB to decide whether detrend & deseasonalize improves MAPE or not
# detrend & deseasonalize need to be applied before extracting lags & means

res_1 = evaluate(
    forecaster=forecaster,
    cv=cv,
    y=y_train,
    X=X_train,
    return_data=True
    )

res_1.mean()

test_MeanAbsolutePercentageError       0.194248
fit_time                               1.617937
pred_time                              0.033730
len_train_window                    1226.000000
dtype: float64

### MAPE heat map 

In [ ]:
# MAPE heat map data
px_data = gscv_results.pivot(
    index='forecaster__window_length',
    columns='forecaster__estimator__n_estimators',
    values='mean_test_MeanAbsolutePercentageError'
    )
px_data.index = px_data.index.astype('str')
px_data.columns = px_data.columns.astype('str')
px_data


In [ ]:
# MAPE heat map plot
fig = px.imshow(
    px_data,
    text_auto=True,
    color_continuous_scale='RdBu_r'
    )
fig.update_xaxes(side="top")
fig.show()


### feature importances

In [ ]:
# refit estimator to get feature_importances_
y_train_trans = pipe.fit_transform(y_train)
forecaster.get_params()['estimator'].fit(y=y_train_trans, X=X_train_trans)


In [ ]:
feature_importances = pd.DataFrame({
    'feature': forecaster.get_params()['estimator'].feature_names_in_,
    'importance': forecaster.get_params()['estimator'].feature_importances_,
    })

feature_importances


In [ ]:
feature_importances.sort_values('importance', ascending=False).set_index('feature').plot()

# fitting

In [81]:
# best_forecaster = rscv.best_forecaster_
best_forecaster = forecaster

all_store_result = pd.DataFrame()

# for store in df_store["store_id"].unique():
for store in df_store["store_id"].unique()[:2]:
    # data
    ts_y = df_store[df_store["store_id"] == store].set_index("date")["sales"]

    # extract lags, means, medians
    df_window = WindowSummarizer(**kwargs).fit_transform(ts_y).dropna()

    # extract DateTimeFeatures
    df_from_y = DateTimeFeatures(ts_freq="D", feature_scope="comprehensive").fit_transform(df_window)
    df_X = df_exog.merge(df_from_y, left_index=True, right_index=True)

    # transform
    df_X_trans = scaler.fit_transform(df_X)
    ts_y_trans = ts_y.tail(len(df_window))
    ts_y_trans.index.freq = 'D'

    cv = SlidingWindowSplitter(
        fh=[i for i in range(1, horizon+1)],
        window_length=(len(ts_y_trans) - horizon * cv_folds),
        step_length=horizon,
        )

    # evaluate
    store_result = evaluate(
        forecaster=best_forecaster, 
        cv=cv, 
        y=ts_y_trans, 
        X=df_X_trans, 
        scoring=MeanAbsoluteScaledError(),
        return_data=True,
        )

    store_result['store_id'] = str(store)
    store_result['mase'] = store_result['test_MeanAbsoluteScaledError']
    store_result['mape'] = [mape(store_result.loc[i,'y_test'], store_result.loc[i,'y_pred']) for i in range(cv_folds)] 
    store_result['mae'] = [mae(store_result.loc[i,'y_test'], store_result.loc[i,'y_pred']) for i in range(cv_folds)] 
    store_result['rmse'] = [rmse(store_result.loc[i,'y_test'], store_result.loc[i,'y_pred']) for i in range(cv_folds)] 
    store_result.drop(columns=["test_MeanAbsoluteScaledError", "fit_time", "pred_time", "len_train_window"], inplace=True)

    all_store_result = pd.concat([all_store_result, store_result])


/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/datatypes/_series/_check.py:43: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  VALID_INDEX_TYPES = (pd.Int64Index, pd.RangeIndex, pd.PeriodIndex, pd.DatetimeIndex)
/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/datatypes/_hierarchical/_check.py:50: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  VALID_INDEX_TYPES = (pd.Int64Index, pd.RangeIndex, pd.PeriodIndex, pd.DatetimeIndex)
/Users/giangphan23/OneDrive - Norges Handelshøyskole/Thesis/Sales_forecast/ap8venv/lib/python3.8/site-packages/sktime/datatypes/_hierarchical/_check.py:51: FutureWarning: pandas.Int64Index is deprecated and will be

In [84]:
all_store_result.groupby('store_id').mean().mean()


cutoff                                            y_train  \
0 2021-01-03  2017-08-20    20.122770
2017-08-21     0.27880...   
1 2021-01-10  2017-08-27    26.070100
2017-08-28     7.36635...   
2 2021-01-17  2017-09-03    16.873060
2017-09-04     4.81842...   
3 2021-01-24  2017-09-10     0.000000
2017-09-11     0.00000...   
0 2021-01-03  2017-08-23     0.000000
2017-08-24     0.00000...   
1 2021-01-10  2017-08-30    12.356000
2017-08-31    10.39418...   
2 2021-01-17  2017-09-06     4.596500
2017-09-07     6.82201...   
3 2021-01-24  2017-09-13    20.684930
2017-09-14     9.24962...   

                                              y_test  \
0  2021-01-04    17.041805
2021-01-05    14.57060...   
1  2021-01-11    16.588700
2021-01-12    20.27640...   
2  2021-01-18    18.799600
2021-01-19    27.78320...   
3  2021-01-25    24.848540
2021-01-26    18.83403...   
0  2021-01-04    10.987803
2021-01-05    15.22061...   
1  2021-01-11     8.271600
2021-01-12    16.20540...   
2  2021-01-18    10.078400
2021-01-19    17.20618...   
3  2021-01-25    17.889600
2021-01-26    18.23920...   

                                              y_pred store_id      mase  \
0  2021-01-04    22.321644
2021-01-05    23.22052...   307222  0.781072   
1  2021-01-11    16.418230
2021-01-12    30.02285...   307222  0.693577   
2  2021-01-18    20.190563
2021-01-19    22.82567...   307222  0.704681   
3  2021-01-25    39.277691
2021-01-26    31.88944...   307222  0.978268   
0  2021-01-04    18.931538
2021-01-05    19.70020...   307244  1.063713   
1  2021-01-11    25.313320
2021-01-12    38.78666...   307244  2.429452   
2  2021-01-18     9.934416
2021-01-19    17.05295...   307244  1.357555   
3  2021-01-25    18.663244
2021-01-26    17.70807...   307244  0.734817   

       mape        mae       rmse  
0  0.306249   7.741814   8.523963  
1  0.214070   6.893241  10.343820  
2  0.203661   6.998171   8.675566  
3  0.271546   9.743870  11.258592  
0  0.399375   8.370063   9.536910  
1  0.622350  19.111455  20.021589  
2  0.442383  10.714603  13.593589  
3  0.244474   5.808222   8.177948

In [35]:
# all_store_result.to_pickle('results/f9/XGB_result_7.pkl')

In [37]:
pd.read_pickle('results/f8/SNAIVE_result_7.pkl').mean()

mae_SNAIVE      8.907645
rmse_SNAIVE    11.243112
mape_SNAIVE     0.418559
mase_SNAIVE     0.898513
dtype: float64

# fitting

In [7]:
from joblib import dump, load
# # Save model
# dump(forecaster, filename='results/f8/XGB_forecaster_7.py')

# # Load model
rscv = load('results/f9/RF_gscv.py')
rscv


ForecastingGridSearchCV(cv=SlidingWindowSplitter(fh=[1, 2, 3, 4, 5, 6, 7], step_length=7,
           window_length=1226),
                        forecaster=TransformedTargetForecaster(steps=[('deseasonalize',
                                                                       Deseasonalizer(sp=7)),
                                                                      ('detrend',
                                                                       Detrender(forecaster=PolynomialTrendForecaster())),
                                                                      ('scale',
                                                                       TabularToSeriesAdaptor(transformer=MinMaxScaler())),
                                                                      ('forecaster',
                                                                       RecursiveTabularRegression..._error'),
                                                                                            

In [8]:
best_pipe = TransformedTargetForecaster([
    ("deseasonalize", Deseasonalizer(model="additive", sp=sp)),
    ("detrend", Detrender(forecaster=PolynomialTrendForecaster(degree=1))),
    ("scale", scaler),
    ("forecaster", rscv.best_forecaster_),
    ])

In [10]:
all_store_result = pd.DataFrame()

# for store in df_store["store_id"].unique():
for store in df_store["store_id"].unique()[:2]:
    # data
    ts_y = df_store[df_store["store_id"] == store].set_index("date")["sales"]

    # extract lags, means, medians
    df_window = WindowSummarizer(**kwargs).fit_transform(ts_y).dropna()

    # extract DateTimeFeatures
    df_from_y = DateTimeFeatures(ts_freq="D", feature_scope="comprehensive").fit_transform(df_window)
    df_X = df_exog.merge(df_from_y, left_index=True, right_index=True)

    # transform
    df_X_trans = scaler.fit_transform(df_X)
    ts_y_trans = ts_y.tail(len(df_window))
    ts_y_trans.index.freq = 'D'

    # evaluate
    store_result = evaluate(
        forecaster=best_pipe, 
        cv=cv, 
        y=ts_y_trans, 
        X=df_X_trans, 
        scoring=MeanAbsoluteScaledError(),
        return_data=True,
        )

    store_result['store_id'] = str(store)
    store_result['mase'] = store_result['test_MeanAbsoluteScaledError']
    store_result['mape'] = [mape(store_result.loc[i,'y_test'], store_result.loc[i,'y_pred']) for i in range(cv_folds)] 
    store_result['mae'] = [mae(store_result.loc[i,'y_test'], store_result.loc[i,'y_pred']) for i in range(cv_folds)] 
    store_result['rmse'] = [rmse(store_result.loc[i,'y_test'], store_result.loc[i,'y_pred']) for i in range(cv_folds)] 
    store_result.drop(columns=["test_MeanAbsoluteScaledError", "fit_time", "pred_time", "len_train_window"], inplace=True)

    all_store_result = pd.concat([all_store_result, store_result])

    print("Finish store ", store)

ValueError: Length of values (4) does not match length of index (5)

# end

In [23]:
SARIMAX_res = pd.read_pickle('results/f8/ARIMA_result_7.pkl')

In [26]:
SARIMAX_res = SARIMAX_res[[
    'store', 
    'mape_ARIMA', 
    'mase_ARIMA',
    'mae_ARIMA', 
    'rmse_ARIMA', 
    'fc_ARIMA',
       ]]
SARIMAX_res


store  mape_ARIMA  mase_ARIMA  mae_ARIMA  rmse_ARIMA  \
0   store_307222     0.28100     0.80050    7.91225     9.09375   
1   store_307244     0.34550     0.85575    6.67450     7.74325   
2   store_307248     0.36300     1.06350    7.31325     8.78150   
3   store_320264     0.39100     0.95450    6.46950     7.86525   
4   store_328165     0.33325     1.17175   25.69050    34.02775   
5   store_349920     0.33125     1.01175   15.03425    18.18750   
6   store_349924     0.27575     0.93700    6.85275     8.36925   
7   store_349952     0.39275     1.25375    8.61725    10.45225   
8   store_349958     0.31375     1.08150    9.48050    11.65875   
9   store_349962     0.34050     0.64650    4.42550     5.26075   
10  store_349972     0.34325     1.20300    9.55725    11.43550   
11  store_349978     0.39650     0.85400    4.52025     5.78050   
12  store_349980     0.30800     1.03500    9.36125    11.85750   
13  store_349998     0.32250     0.98650    5.27775     6.52475   
14  store_350016     0.35475     1.72350    9.14000    12.06550   
15  store_350018     0.30950     1.35225   19.38725    25.26475   
16  store_350026     0.35000     0.94875    4.02375     4.61050   
17  store_350028     0.31700     0.64800    2.96800     3.64450   
18  store_350040     0.39400     0.90575    7.18725     8.80750   
19  store_350046     0.29425     0.67750    2.85675     3.80750   
20  store_350054     0.29175     1.26400    7.48525    10.12550   
21  store_350056     0.50050     1.17375    3.75325     4.78925   
22  store_350060     0.27275     1.12800    7.90200     9.04575   
23  store_354468     0.47525     0.98950    3.37525     4.37100   
24  store_387240     0.37350     0.85750    3.67600     4.43775   
25  store_412585     0.50525     1.40425    4.79600     6.21400   
26  store_441997     0.27925     0.67700    3.14950     4.30375   
27  store_452387     0.38125     1.34400    9.12925    11.45725   
28  store_461349     0.51725     1.13175    5.24450     6.86075   
29  store_464495     0.46000     0.99600    3.46725     4.25425   
30  store_471477     0.40350     1.07400    4.95575     5.62475   
31  store_476061     0.58650     0.69800    2.57200     3.03825   
32  store_480733     0.38650     1.41000    9.70750    11.67675   
33  store_528854     0.36250     1.27650   14.44150    18.59625   
34  store_536898     0.40775     0.91900    3.62100     4.70050   
35  store_536902     0.35250     0.90525    4.11025     5.32200   
36  store_566790     0.46550     0.97225   15.45150    18.86900   
37  store_566792     0.58100     0.83300    4.31900     5.30300   

                                             fc_ARIMA  
0   [34.66248403616754, 28.328400365946095, 22.329...  
1   [13.835429749967066, 13.977082334680194, 13.18...  
2   [20.370068633697326, 15.048735970050245, 12.96...  
3   [23.824847833579213, 15.790110510681625, 9.840...  
4   [88.15915634559391, 66.91400890470602, 47.5110...  
5   [48.68037935786861, 39.085028199010125, 31.009...  
6   [16.94172908342006, 18.40541647990217, 15.8964...  
7   [11.995581601200442, 12.43272669371141, 12.795...  
8   [30.7070560345227, 24.869585991353052, 21.3462...  
9   [9.11683926020528, 7.086906513232132, 7.159068...  
10  [26.60429278917856, 22.608660245194244, 16.117...  
11  [5.396586011699251, 6.357230579548666, 6.60789...  
12  [31.442662612793022, 24.00167554721486, 18.264...  
13  [16.50143560348378, 13.328888819959197, 10.901...  
14  [26.987285904677833, 23.433381599079038, 18.40...  
15  [49.167015393947075, 38.53260851485853, 35.084...  
16  [11.53610968578011, 11.018451743623693, 8.5453...  
17  [6.596427781569213, 5.799914475385427, 6.64632...  
18  [11.806586059818901, 13.359657861956709, 11.69...  
19  [4.923734925865462, 5.48275564665126, 5.758125...  
20  [34.75810386672144, 28.240301563761317, 25.517...  
21  [9.915778844015861, 7.8865648048299795, 6.4928...  
22  [30.251371692848593, 26.460661109026532, 23.56...  
23  [7.575378125888776, 6.506772175473843, 5.57549...

In [27]:
round(SARIMAX_res.describe(), 2)


mape_ARIMA  mase_ARIMA  mae_ARIMA  rmse_ARIMA
count       38.00       38.00      38.00       38.00
mean         0.38        1.03       7.47        9.32
std          0.08        0.24       4.94        6.42
min          0.27        0.65       2.57        3.04
25%          0.32        0.87       4.05        4.91
50%          0.36        0.99       6.57        7.80
75%          0.40        1.17       9.14       11.45
max          0.59        1.72      25.69       34.03

In [42]:
y_pred = SARIMAX_res.iloc[0,5]
y_true = df_store[df_store['store_id']==307222].set_index('date')['sales'][-7:]

from plotly import graph_objects as go
fig = go.Figure()

fig.add_trace(go.Scatter(x=y_true.index, 
                         y=y_true, 
                         name='Test set',
                         line={'color': 'dodgerblue'},
                         ))
fig.add_trace(go.Scatter(x=y_true.index, 
                         y=y_pred, 
                         name='Forecast',
                         line={'color': 'salmon', 'dash': 'dash'},
                         ))
fig.update_layout(title='SARIMAX forecast')
fig.update_yaxes(title_text='Sales in million VND')

fig.show()


In [ ]:
import plotly.io as pio
pio.orca.config.timeout = 3600
pio.orca.config.default_scale = 8
pio.orca.config.default_width = 800
fig.write_image(file="results/plots/fc_snaive_7.png")